In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import os
import gc
import glob
import numba
import numpy.linalg as la
from scipy import stats
from scipy.stats import circmean
from scipy.optimize import linear_sum_assignment
from scipy.spatial.distance import cdist

In [41]:
foldername = 'ffC4'
n_inds = 10

window_size = '07' # sliding window size in seconds
fps = 10

angle_thresh = np.cos(np.pi/6)
time_thresh = 5

In [42]:
df = pd.read_csv('/Users/vivekhsridhar/Library/Mobile Documents/com~apple~CloudDocs/Documents/Code/DirectionalCorrelation/Data/Output/pigeons/' + str(n_inds) + '_birds/' + foldername + '/' + 'alltracks.csv')
df.head()

Unnamed: 0  #t(centisec)    X(m)    Y(m)    speed  acceleration     dir_x  \
0           0           0.0 -0.3002  3.0477  0.21717      0.281587 -0.973892   
1           1           0.0 -0.3002  3.0477  0.21717      0.281587 -0.973892   
2           2           0.0 -0.3002  3.0477  0.21717      0.281587 -0.973892   
3           3           0.0 -0.3002  3.0477  0.21717      0.281587 -0.973892   
4           4           0.0 -0.3002  3.0477  0.21717      0.281587 -0.973892   

      dir_y  f_id  n_id  ...  acc_diff  dev_gspeed  dev_ngspeed  dev_gacc  \
0  0.227011     0     0  ...  0.000000   -0.355163    -0.355163 -0.353035   
1  0.227011     0     1  ...  0.592826   -0.355163     0.115862 -0.353035   
2  0.227011     0     2  ...  2.970756   -0.355163     0.718222 -0.353035   
3  0.227011     0     3  ...  1.960514   -0.355163     0.200896 -0.353035   
4  0.227011     0     4  ... -0.234571   -0.355163    -0.565610 -0.353035   

   dev_ngacc  rotated_x  rotated_y      dist  ang_pos_x  ang_pos_y  
0  -0.353035   1.527619   0.039977  0.000000        NaN        NaN  
1   0.239791   1.527619   0.039977  1.567878   0.623805   0.781580  
2   2.617721   1.527619   0.039977  3.247802   0.716277  -0.697816  
3   1.607479   1.527619   0.039977  0.851654  -0.513809   0.857905  
4  -0.587606   1.527619   0.039977  2.644683   0.989346   0.145586  

[5 rows x 21 columns]

#### Rescale trajectory data to match the timescale of directional correlations while retaining pairwise nature of the measures

In [4]:
for fr in range(int(window_size)*fps//2, int(df['#t(centisec)'].max() - int(window_size)*fps//2)):
    tmp = df[(df['#t(centisec)'] >= fr - int(window_size)*fps//2) & (df['#t(centisec)'] <= fr + int(window_size)*fps//2)]

    tmp1 = tmp.loc[:,["f_id", "n_id", "dist", "speed_diff", "acc_diff"]]
    tmp2 = tmp.loc[:,["f_id", "n_id", "ang_pos_x", "ang_pos_y"]]

    tmp_ord1 = tmp1.groupby(['f_id', 'n_id']).median()
    tmp_ord1 = tmp_ord1.reset_index()
    tmp_ord1 = tmp_ord1.rename(index=str, columns={'dist':'dist', 'speed_diff':'speed_diff', 'acc_diff':'acc_diff'})
    tmp_ord2 = tmp2.groupby(['f_id', 'n_id']).mean()
    tmp_ord2 = tmp_ord2.reset_index()
    tmp_ord2 = tmp_ord2.rename(index=str, columns={'ang_pos_x':'ang_pos_x', 'ang_pos_y':'ang_pos_y'})
    
    tmp_ord = pd.merge(tmp_ord1, tmp_ord2, how='left')
    tmp_ord['#t(centisec)'] = fr
    
    df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
        
df_rescaled.head()

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

...

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_rescaled = tmp_ord if fr == int(window_size)*fps//2 else df_rescaled.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/466100100.py:17: Fut

f_id  n_id      dist  speed_diff  acc_diff  ang_pos_x  ang_pos_y  \
0     0     0  0.000000    0.000000  0.000000        NaN        NaN   
1     0     1  4.487205    0.367841  0.101317  -0.055651   0.056564   
2     0     2  3.947398   -0.139183  0.042549  -0.200161   0.147215   
3     0     3  2.294148   -0.302900 -0.087998   0.001462   0.014840   
4     0     4  6.110898    0.472410  0.320212  -0.168921   0.121691   

   #t(centisec)  
0           300  
1           300  
2           300  
3           300  
4           300

#### Rescale trajectory data to match timescale of directional correlations and get individual level measures

In [5]:
for fr in range(int(window_size)*fps//2, int(df['#t(centisec)'].max() - int(window_size)*fps//2)):
    tmp = df[(df['#t(centisec)'] >= fr - int(window_size)*fps//2) & (df['#t(centisec)'] <= fr + int(window_size)*fps//2)]

    tmp1 = tmp.loc[:,["f_id", "speed", "acceleration", "dev_gspeed", "dev_gacc"]]
    tmp2 = tmp.loc[:,["f_id", "rotated_x", "rotated_y"]]

    tmp_ord1 = tmp1.groupby(['f_id']).median()
    tmp_ord1 = tmp_ord1.reset_index()
    tmp_ord1 = tmp_ord1.rename(index=str, columns={'speed':'speed', 'acceleration':'acceleration', 'dev_gspeed':'dev_gspeed', 'dev_gacc':'dev_gacc'})
    tmp_ord2 = tmp2.groupby(['f_id']).mean()
    tmp_ord2 = tmp_ord2.reset_index()
    tmp_ord2 = tmp_ord2.rename(index=str, columns={'rotated_x':'rx', 'rotated_y':'ry'})
    
    tmp_ord = pd.merge(tmp_ord1, tmp_ord2, how='left')
    tmp_ord['#t(centisec)'] = fr
    
    df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
        
df2.head()

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

...

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df2 = tmp_ord if fr == int(window_size)*fps//2 else df2.append(tmp_ord)
/var/folders/ng/l4j590g95vl5r33ctw59y6cr0000gn/T/ipykernel_33612/427452606.py:17: FutureWarning: The frame.append method is deprecate

f_id      speed  acceleration  dev_gspeed  dev_gacc        rx        ry  \
0     0  13.159371      5.737441   -0.078075 -0.060491  0.903427 -0.268378   
1     1  13.545980      6.042761    0.117942  0.059617  0.282477  0.656158   
2     2  13.037266      5.681452   -0.241997 -0.031166  0.748740  0.142207   
3     3  13.153884      5.571784   -0.388306 -0.165494  0.789277 -1.130338   
4     4  13.754853      5.991597    0.218665  0.184746 -1.647200  0.726583   

   #t(centisec)  
0           300  
1           300  
2           300  
3           300  
4           300

In [6]:
del tmp
del tmp1
del tmp2
del tmp_ord1
del tmp_ord2
del tmp_ord
gc.collect()

16

### Handle directional correlation data
Below, we binarise pairwise output obtained from the directional correlation cuda code. We then convert this measure of leadership per individual per frame.

#### Binarise pairwise events to 'leadership' or 'not leadership'

In [7]:
dcorr = pd.read_csv("/Users/vivekhsridhar/Library/Mobile Documents/com~apple~CloudDocs/Documents/Code/DirectionalCorrelation/Data/Output/pigeons/" + str(n_inds) + "_birds/" + foldername + '/cross_correlation_' + window_size + '.csv')
dcorr.columns = ['#t(centisec)', 'f_id', 'n_id', 'tau', 'cc']

dcorr.loc[dcorr['cc'] < angle_thresh,'cc'] = 0
dcorr.loc[np.abs(dcorr['tau']) <= time_thresh/3,'tau'] = 0

@numba.njit(fastmath=True, parallel=True)
def binarise_leadership(frame, f_id, tau, cc):
    cc_out = np.zeros(cc.shape)
    frs = np.unique(frame)
    f_ids = np.unique(f_id)
    for fr in numba.prange(frs.shape[0]):
        for idx in numba.prange(f_ids.shape[0]):
            subset_idxs = np.where((frame == frs[fr]) & (f_id == f_ids[idx]) & (tau < 0))[0]
            if len(subset_idxs) > 0:
                ccvals = cc[subset_idxs]
                if ccvals.max() > angle_thresh:
                    max_idx = subset_idxs[np.where(ccvals == ccvals.max())[0]]
                    cc_out[max_idx] = 1
    
    return cc_out

In [8]:
frame = dcorr['#t(centisec)'].values
f_id = dcorr['f_id'].values
tau = dcorr['tau'].values
cc = dcorr['cc'].values

dcorr['cc'] = binarise_leadership(frame, f_id, tau, cc)

#### Convert 'leadership' to an individual level metric over time (rather than a pairwise metric)

In [9]:
@numba.njit(fastmath=True, parallel=True)
def individual_leadership(frame, f_id, n_id, cc):
    fr_out = np.zeros((np.unique(frame).shape[0]*n_inds,), dtype=np.int64)
    fid_out = np.zeros((np.unique(frame).shape[0]*n_inds,), dtype=np.int64)
    lscore = np.zeros((np.unique(frame).shape[0]*n_inds,), dtype=np.float64)
    
    frs = np.unique(frame)
    f_ids = np.unique(f_id)
    for fr in numba.prange(frs.shape[0]):
        for idx in numba.prange(f_ids.shape[0]):
            lead_idxs = np.where((frame == frs[fr]) & (n_id == f_ids[idx]))[0]
            follow_idxs = np.where((frame == frs[fr]) & (f_id == f_ids[idx]))[0]
            
            fr_out[fr*n_inds + idx] = frs[fr]
            fid_out[fr*n_inds + idx] = f_ids[idx]
            lscore[fr*n_inds + idx] = np.sum(cc[lead_idxs]) - np.sum(cc[follow_idxs])
            
    return fr_out, fid_out, lscore

In [10]:
frame = dcorr['#t(centisec)'].values
f_id = dcorr['f_id'].values
n_id = dcorr['n_id'].values
cc = dcorr['cc'].values

fr_out, fid_out, lscore = individual_leadership(frame, f_id, n_id, cc)

In [11]:
dcorr2 = pd.DataFrame(np.array([fr_out, fid_out, lscore]).T, columns=['#t(centisec)', 'f_id', 'lscore'])
dcorr2['lscore'] /= n_inds

tmp = dcorr2.loc[:,["f_id", "lscore"]]
tmp_ord = tmp.groupby(['f_id']).sum()
tmp_ord = tmp_ord.reset_index()
tmp_ord = tmp_ord.rename(index=str, columns={'lscore':'lfinal'})

dcorr2 = pd.merge(dcorr2, tmp_ord, how='left')
dcorr2.head()

#t(centisec)  f_id  lscore  lfinal
0         300.0   0.0     0.3   717.6
1         300.0   1.0     0.0   350.2
2         300.0   2.0     0.1  -233.1
3         300.0   3.0     0.1   163.5
4         300.0   4.0    -0.1  -296.1

### Create final datasets - individual and pairwise
These two dataframes will contain all data about morphology, movement, vision and leadership. The only way the two dataframes differ is based on whether the data is presented at the individual or pairwise level.

#### Individual data

In [12]:
df = pd.merge(df2, dcorr2)

cols = ['#t(centisec)', 'f_id']
df[cols] = df[cols].astype(np.int32)

df.head()

f_id      speed  acceleration  dev_gspeed  dev_gacc        rx        ry  \
0     0  13.159371      5.737441   -0.078075 -0.060491  0.903427 -0.268378   
1     1  13.545980      6.042761    0.117942  0.059617  0.282477  0.656158   
2     2  13.037266      5.681452   -0.241997 -0.031166  0.748740  0.142207   
3     3  13.153884      5.571784   -0.388306 -0.165494  0.789277 -1.130338   
4     4  13.754853      5.991597    0.218665  0.184746 -1.647200  0.726583   

   #t(centisec)  lscore  lfinal  
0           300     0.3   717.6  
1           300     0.0   350.2  
2           300     0.1  -233.1  
3           300     0.1   163.5  
4           300    -0.1  -296.1

In [13]:
df.to_csv('/Users/vivekhsridhar/Library/Mobile Documents/com~apple~CloudDocs/Documents/Code/DirectionalCorrelation/Data/Output/pigeons/' + str(n_inds) + '_birds/' + foldername + '/' + 'individual_' + window_size + '.csv', mode='w')

#### Pairwise data

In [ ]:
df = pd.merge(df_rescaled, dcorr)

cols = ['#t(centisec)', 'f_id', 'n_id', 'tau']
df[cols] = df[cols].astype(np.int32)

df.head()

In [ ]:
df['ang_pos'] = np.arctan2(df['ang_pos_y'], df['ang_pos_x'])
df['ang_pos'] = np.abs(df['ang_pos'])

df.drop(['ang_pos_x', 'ang_pos_y'], axis=1, inplace=True) 

In [ ]:
df.to_csv('/Users/vivekhsridhar/Library/Mobile Documents/com~apple~CloudDocs/Documents/Code/DirectionalCorrelation/Data/Output/pigeons/' + str(n_inds) + '_birds/' + foldername + '/' + 'pairwise_' + window_size + '.csv', mode='w')